In [1]:
import os
localfs_path = os.environ.get('SCRATCH_LOCAL') + '/'

In [2]:
os.environ['_JAVA_OPTIONS'] = f'-Djava.io.tmpdir={localfs_path}'

import hail as hl

hl.init(
    tmp_dir=(localfs_path+'tmp_hail_3'),
    spark_conf={'spark.driver.memory': '10G', 'spark.executor.memory': '10G'},
    default_reference='GRCh38'
) 

Picked up _JAVA_OPTIONS: -Djava.io.tmpdir=/localfs/4515459/
Picked up _JAVA_OPTIONS: -Djava.io.tmpdir=/localfs/4515459/


23/08/22 13:47:00 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
Running on Apache Spark version 3.3.2
SparkUI available at http://ac0056:4040
Welcome to
     __  __     <>__
    / /_/ /__  __/ /
   / __  / _ `/ / /
  /_/ /_/\_,_/_/_/   version 0.2.113-cf32652c5077
LOGGING: writing to /net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/preprocessing/oligogenic-model/hail-20230822-1346-0.2.113-cf32652c5077.log


In [3]:
from hail.plot import show
from pprint import pprint
from bokeh.layouts import gridplot
import numpy as np
hl.plot.output_notebook()
import bokeh

from bokeh.plotting import figure, output_notebook, show
output_notebook

Loading BokehJS ...

<function bokeh.io.output.output_notebook(resources=None, verbose=False, hide_banner=False, load_timeout=5000, notebook_type='jupyter')>

In [4]:
%load_ext autoreload
%autoreload 2

In [5]:
from oligogenic_model import (
    read_in_pheno_anno_pw,
    aggregate_per_burden,
    stand_burden,
    stand_with_ref,
    read_in_pheno_anno_sport,
    model_assignment,
    read_in_pheno_anno_all
)

### Use average burden from cohort to standardize

In [6]:
mt = hl.read_matrix_table(
    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/mts/oligogenic-model/gts_and_s.mt'
)

In [8]:
mt = mt.naive_coalesce(500)

In [ ]:
mt = mt.checkpoint(localfs_path+'gts_and_s_rep.mt')

In [ ]:
mt = read_in_pheno_anno_sport(
    localfs_path+'gts_and_s_rep.mt',
    'gts_sport_1')

In [ ]:
#exclude low quality samples

to_exclude = ['S_7288', 'S_7289', 'S_7290', 'WGS_6827', 'WGS_6835', 'WGS_5', 'WGS_8']#, 'B502', 'B506']

mt = mt.filter_cols(
    hl.literal(to_exclude).contains(mt.s),
    keep = False
) 

mt = mt.distinct_by_col()

In [ ]:
results = aggregate_per_burden(mt, 'gts_sport_12')

results = stand_burden(results, 'gts_sport_13')

In [8]:
results = hl.read_matrix_table(localfs_path+'gts_sport_13stand_per_gene.mt')

In [9]:
cadds = [0,5,10,16]

In [10]:
results.count()

(17844, 203)

In [11]:
results = results.annotate_cols(
    skat_pheno = hl.if_else(
        results.group == 'GTS',
        hl.if_else(
            results.phenotypes.phenotype == 'GTS',
            'YES',
            'NO'),
        'NO'
    )
)

results.aggregate_cols(hl.agg.counter(results.skat_pheno))

{'NO': 157, 'YES': 46}

In [12]:
genes = ['CHADL', 'DRD2', 'MAOA', 'PCDH10', 'HTR2A', 'SLITRK5', 'SORCS3', 'KCNQ5', 'CDH9', 'CHD8', 'PCDH1']

In [13]:
group, sport, model_sum, model_weits = model_assignment(results, genes)

## Now run the oligogenic model with MAF filter


In [24]:
mt_maf =  hl.read_matrix_table('/localfs/4515459/gts_sport_1.mt')

In [25]:
mt_maf = mt_maf.filter_rows(
    mt_maf.gnomad_v_3_1.freq.AF[2] < 0.0001
)

mt_maf = mt_maf.checkpoint(
    localfs_path+'mt_filt.mt'
)

2023-08-21 22:04:20.779 Hail: INFO: wrote matrix table with 658698 rows and 204 columns in 488 partitions to /localfs/4515459/mt_filt.mt


In [26]:
to_exclude = ['S_7288', 'S_7289', 'S_7290', 'WGS_6827', 'WGS_6835', 'WGS_5', 'WGS_8']

mt_maf = mt_maf.filter_cols(
    hl.literal(to_exclude).contains(mt_maf.s),
    keep = False
) 

mt_maf = mt_maf.distinct_by_col()

In [27]:
results_maf = aggregate_per_burden(mt_maf, 'gts_sport_maf_111')
results_maf = stand_burden(results_maf, 'gts_sport_122')

2023-08-21 22:04:38.854 Hail: INFO: wrote matrix table with 658698 rows and 203 columns in 488 partitions to /localfs/4515459/gts_sport_maf_111.mt
2023-08-21 22:04:44.532 Hail: INFO: Ordering unsorted dataset with network shuffle
2023-08-21 22:05:22.149 Hail: INFO: wrote matrix table with 17695 rows and 203 columns in 488 partitions to /localfs/4515459/gts_sport_maf_111per_burden_agg.mt
2023-08-21 22:05:28.917 Hail: INFO: wrote matrix table with 17695 rows and 203 columns in 488 partitions to /localfs/4515459/gts_sport_122stand_per_gene.mt


In [14]:
results_maf = hl.read_matrix_table(localfs_path+'gts_sport_122stand_per_gene.mt')

In [15]:
results_maf = results_maf.annotate_cols(
    skat_pheno = hl.if_else(
        results_maf.group == 'GTS',
        hl.if_else(
            results_maf.phenotypes.phenotype == 'GTS',
            'YES',
            'NO'),
        'NO'
    )
)

results_maf.aggregate_cols(hl.agg.counter(results_maf.skat_pheno))

{'NO': 157, 'YES': 46}

In [16]:
group, sport, model_sum_maf, model_weits_maf = model_assignment(results_maf, genes)

In [17]:
from bokeh.models import Label, LabelSet

colors = bokeh.palettes.Category20[16]

y = np.linspace(0,1)
x = np.linspace(0,1,100)

from bokeh.plotting import figure, output_notebook, show

output_notebook

p = figure(plot_width=800, plot_height=800)

for o in [model_sum, model_weits]:

    for i in range(len(o)):

        start = np.min(o[i])-1
        stop = np.max(o[i])+1

        false_pos = []
        true_pos = []

        for x in np.linspace(start,stop,20000):
            false_pos.append(np.sum((o[i] > x)[group == 0])/157)
            true_pos.append(np.sum((o[i] > x)[group == 1])/46)
            
        print(i)
        print(-np.trapz(true_pos, false_pos))

        p.line(false_pos, true_pos, line_width=0.5, line_color='grey')
        
for o in [model_sum_maf, model_weits_maf]:

    for i in range(len(o)):

        start = np.min(o[i])-1
        stop = np.max(o[i])+1

        false_pos = []
        true_pos = []

        for x in np.linspace(start,stop,20000):
            false_pos.append(np.sum((o[i] > x)[group == 0])/157)
            true_pos.append(np.sum((o[i] > x)[group == 1])/46)

        print(i)
        print(-np.trapz(true_pos, false_pos))
        
        p.line(false_pos, true_pos, line_width=0.5, line_color='grey')
        
        
start = np.min(model_sum_maf[0])-1
stop = np.max(model_sum_maf[0])+1

false_pos = []
true_pos = []

for x in np.linspace(start,stop,20000):
    false_pos.append(np.sum((model_sum_maf[0] > x)[group == 0])/157)
    true_pos.append(np.sum((model_sum_maf[0] > x)[group == 1])/46)

p.line(false_pos, true_pos, line_width=4, line_color='orange')
        
p.line([0, 0.5, 1], [0, 0.5, 1])

p.circle(0.43949, 0.617, size=12, color="darkred", alpha=1)

p.xaxis.axis_label = 'false positives'
p.yaxis.axis_label = 'true positives'

p.xaxis.axis_label_text_font_size = "15pt"
p.xaxis.major_label_text_font_size = "15pt"
p.yaxis.axis_label_text_font_size = "15pt"
p.yaxis.major_label_text_font_size = "15pt"

show(p)

0
0.5726945444475214
1
0.5188313486568817
2
0.5283854887842703
3
0.41698975353087786
0
0.5467322071448352
1
0.5274162281916367
2
0.5157158681805594
3
0.4157435613403489
0
0.6069648296870672
1
0.5546247576848518
2
-0.0
3
-0.0
0
0.5935336471891443
1
0.5591941290501247
2
-0.0
3
-0.0


In [ ]:
print(-np.trapz(true_pos, false_pos))

In [85]:
 # auc of the second-best model 0.59

## Get the best point on the curve

In [42]:
sensitivity = np.array(true_pos)
specificity = 1-np.array(false_pos)

In [43]:
measure = sensitivity+specificity

In [44]:
np.max(measure)

1.232484076433121

In [45]:
np.where(measure == np.max(measure))

(array([4952, 4953, 4954, 4955, 4956, 4957, 4958, 4959, 4960, 4961, 4962,
        4963, 4964, 4965, 4966, 4967, 4968, 4969, 4970, 4971, 4972, 4973,
        4974, 4975, 4976, 4977, 4978, 4979, 4980, 4981, 4982, 4983, 4984,
        4985, 4986, 4987, 4988, 4989, 4990, 4991, 4992, 4993, 4994, 4995,
        4996, 4997, 4998, 4999, 5000, 5001, 5002, 5003, 5004, 5005, 5006,
        5007, 5008, 5009, 5010, 5011, 5012, 5013, 5014, 5015, 5016, 5017,
        5018, 5019, 5020, 5021, 5022, 5023, 5024, 5025, 5026]),)

In [46]:
np.linspace(start,stop,20000)[4985]

1.174960464913874

In [47]:
true_pos[4985]

0.5

In [48]:
false_pos[4985]

0.267515923566879

In [49]:
(model_sum_maf[0] > 1.15)[group == 1]

array([ True,  True, False,  True,  True,  True,  True,  True, False,
        True, False, False,  True, False, False,  True,  True,  True,
       False,  True, False, False,  True, False, False, False, False,
       False,  True,  True,  True,  True, False, False,  True, False,
        True,  True, False, False,  True, False, False, False,  True,
       False])

## Get random models (fpr)

In [51]:
all_genes = list(set(results.nearest_genes_20kb.collect()))

In [52]:
gts_genes = ['DCC', 'RBFOX', 'SLC30A9', 'DCAF4L1', 'SORCS3', 'KCNQ5', 'KCNQ-IT1', 'APOPT1', 'C14orf2', 'NAA11', 'NEGR1',
        'CHADL', 'SOX5', 'PANK2', 'COL27A1', 'PDGFB', 'CELSR3', 'OPA1', 'FBN2', 'WWC1', 'NIPBL', 
             'FN1', 'FBN2', 'SLITRK1', 'SLITRK2', 'SLITRK3', 'SLITRK4', 'SLITRK5', 'SLITRK6', 
             'HDC', 'OPRK1', 'PCDH10', 'NTSR2', 'CHD8', 'SCUBE1', 'PNKD', 'CNTNAP2', 'MOG', 
             'DRD2', 'DRD3', 'DRD4', 'DRD5', 'DAT1', 'DBH', 'HTR2A', 'TPH2', 'EAAT1', 'SAPAP3',
            'CTNNA3', 'NLGN4', 'FSCB', 'IMMP2L', 'NRXN1', 'AADAC', 'DBH', 'MAOA', 'HTR1A', 'HTR2C', 'SLC6A4',
             'TPH2', 'COL27A1', '5-HTTLPR', 'EAAT1', 'COL8A1', 'KCNE1', 'KCNE2',
         'RICTOR', 'WWC1',
        'CELSR3, NIPBL', 'FN1', 'PNKD', 'CDH26', 'CADM2', 'OPCML', 'CDH9',
         'NCAM2', 'CD47', 'CDH5', 'CADM4', 'C1QBP', 'CTTN', 'LSAMP',
         'PKP4', 'PCDH1', 'CNTNAP2', 'MBP', 'GABBR2', 'GABBR2', 'GRIK4', 'NCR1', 'FLT3', 'IL12A', 'HDAC9',
         'CD180', 'CDH26', 'NCAM2', 'NTM', 'ROBO2', 'NR2F1', 'ASH1L', 'FLT3']

In [53]:
all_genes = [g for g in all_genes if g not in gts_genes]

In [54]:
len(all_genes)

17769

In [ ]:
model_weits_rand = []
model_sum_rand = []
false_pos_rand = []
true_pos_rand = []
aucs = []

for i in range(1000):
    
    genes = np.random.randint(17769, size=11)
    sel_genes = [all_genes[idx] for idx in genes]
    
    group, sport, model_sum, model_weits = model_assignment(results_maf, sel_genes)
    
    false_pos = []
    true_pos = []
    
    start = np.min(model_sum[0])-1
    stop = np.max(model_sum[0])+1
    
    for x in np.linspace(start,stop,20000):
        false_pos.append(np.sum((model_sum[0] > x)[group == 0])/157)
        true_pos.append(np.sum((model_sum[0] > x)[group == 1])/46)
        
    print(-np.trapz(true_pos, false_pos))
    
    model_weits_rand.append(model_weits)
    model_sum_rand.append(model_sum)
    false_pos_rand.append(false_pos)
    true_pos_rand.append(true_pos)
    aucs.append(-np.trapz(true_pos, false_pos))

-0.0
0.47514538908889503


In [ ]:
true_pos_rand = np.array(true_pos_rand)

np.save(
    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/oligogenic-auc/true_pos_rand_sum_maf.npy',
    true_pos_rand
)

In [ ]:
true_pos_rand = np.load(
    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/oligogenic-auc/true_pos_rand_sum_maf.npy'
)

In [ ]:
false_pos_rand = np.array(false_pos_rand)

np.save(
    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/oligogenic-auc/false_pos_rand_sum_maf.npy',
    false_pos_rand
)

In [ ]:
false_pos_rand = np.load(
    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/oligogenic-auc/false_pos_rand_sum_maf.npy'
)

In [72]:
np.percentile(aucs, 95)

0.5986603433951814

In [77]:
np.percentile(aucs, 96.6)

0.6069003046247577

In [ ]:
p = figure(plot_width=800, plot_height=800)

for t, f in zip(true_pos_rand[0:100],false_pos_rand[0:100]):
    p.line(f, t, line_width=0.1, line_color='grey')
    
p.line(false_pos, true_pos, line_width=4, line_color='orange')

p.line([0, 0.5, 1], [0, 0.5, 1])
p.xaxis.axis_label = 'false positives'
p.yaxis.axis_label = 'true positives'

p.xaxis.axis_label_text_font_size = "15pt"
p.xaxis.major_label_text_font_size = "15pt"
p.yaxis.axis_label_text_font_size = "15pt"
p.yaxis.major_label_text_font_size = "15pt"

In [ ]:
show(p)

# Explore percentage with tics

In [9]:
mt = read_in_pheno_anno_all(
    '/net/pr2/projects/plgrid/plggneuromol/imdik-zekanowski-gts/data/mts/oligogenic-model/gts_and_s.mt',
    'all_for_hist')

2023-05-31 21:46:41.211 Hail: INFO: Reading table without type imputation
  Loading field 'f0' as type str (not specified)
  Loading field 'f1' as type str (not specified)
  Loading field 'f2' as type str (not specified)
  Loading field 'f3' as type str (not specified)
  Loading field 'f4' as type str (not specified)
  Loading field 'f5' as type str (not specified)
  Loading field 'f6' as type str (not specified)
  Loading field 'f7' as type str (not specified)
  Loading field 'f8' as type str (not specified)
2023-05-31 21:46:42.225 Hail: INFO: Reading table without type imputation
  Loading field 'Gene stable ID' as type str (not specified)
  Loading field 'UniProtKB Gene Name symbol' as type str (not specified)
2023-05-31 21:46:43.660 Hail: INFO: Reading table to impute column types
2023-05-31 21:46:44.664 Hail: INFO: Finished type imputation
  Loading field 'ID' as type str (imputed)
  Loading field 'family' as type str (imputed)
  Loading field 'sex' as type str (imputed)
  Loading

In [10]:
results = aggregate_per_burden(mt, 'all_for_hist_2')

2023-05-31 22:19:06.701 Hail: INFO: wrote matrix table with 6538550 rows and 287 columns in 488 partitions to /localfs/3082338/all_for_hist_2.mt
2023-05-31 22:31:41.978 Hail: INFO: Ordering unsorted dataset with network shuffle
2023-05-31 22:32:33.075 Hail: INFO: wrote matrix table with 17844 rows and 287 columns in 488 partitions to /localfs/3082338/all_for_hist_2per_burden_agg.mt


In [11]:
results = stand_burden(results, 'all_for_hist_3')

2023-05-31 22:32:41.454 Hail: INFO: wrote matrix table with 17844 rows and 287 columns in 488 partitions to /localfs/3082338/all_for_hist_3stand_per_gene.mt


In [ ]:
reference = 